# 新旧个税机制全透析

作者：Symbol, PKUJohnson

税制改革到来，新税制部分改动在10月1日即将生效，按理说这是件利国利民的大好事。

正在吃瓜看世界杯的我，无意间看到了一篇“实质增税的个税改革方案”的文章，吓得我瓜都掉了，不是说好的降税么，怎么就变成增税了？？？

世界杯也不看了，赶紧代码码起来，数据说话。

## 第一部分：先了解新老税制规则

### 1. 现行税制规则

现行个人所得税征收由两部分构成：

一、工资部分，按月缴纳规则如下：

免征额：3500，超过部分按照如下阶梯税率收取

|全月应纳税所得额|税率 |速算扣除数（元）|
|--------------|----|---------------|
|全月应纳税所得额不超过1500元|3%|0|
|全月应纳税所得额超过1500元至4500元|10%|105|
|全月应纳税所得额超过4500元至9000元|20%|555|
|全月应纳税所得额超过9000元至35000元|25%|1005|
|全月应纳税所得额超过35000元至55000元|30%|2755|
|全月应纳税所得额超过55000元至80000元|35%|5505|
|全月应纳税所得额超过80000元|45%|13505|

二、年终奖扣税方式为：年终奖*税率-速算扣除数，税率是按年终奖/12作为“应纳税所得额”对应的税率。

### 2.新税制规则

新税率规则下，工资和年终奖合并计算，折合到每月扣除，按照如下阶梯税率收取。

免征额：提高到5000，超出部分阶梯税率如下：

|全月应纳税所得额|税率 |速算扣除数（元）|
|--------------|----|---------------|
|全月应纳税所得额不超过3000元|3%|0|
|全月应纳税所得额超过3000元至12000元|10%|210|
|全月应纳税所得额超过12000元至25000元|20%|1410|
|全月应纳税所得额超过25000元至35000元|25%|2660|
|全月应纳税所得额超过35000元至55000元|30%|4410|
|全月应纳税所得额超过55000元至80000元|35%|7160|
|全月应纳税所得额超过80000元|45%|15160|


## 第二部分：工欲善其事，必先利其器，先搞个新旧税制纳税计算器

In [71]:
# 当前阶梯税率和免税额度
rate_level_old = [(0,1500,0.03, 0),(1500, 4500, 0.1, 105),(4500, 9000, 0.2, 555),
                  (9000,35000,0.25,1005),(35000,55000,0.3,2755),(55000,80000,0.35,5505),(80000,999999999,0.45,13505)]
duty_free_old = 3500

# 新版阶梯税率和免税额度
rate_level_new = [(0,3000,0.03),(3000,12000,0.1),(12000,25000,0.2),(25000,35000,0.25),
                  (35000, 55000,0.3),(55000,80000,0.35), (80000,999999999,0.45)]
duty_free_new = 5000

# 计算奖金纳税数（当前税制）
def get_tax_bonus(bonus):
    incm = bonus / 12.0
    for r_info in rate_level_old:
        if incm > r_info[0] and incm <= r_info[1]:
            return bonus * r_info[2] - r_info[3]
    return 0    

# 按照阶梯税率计算税额
def get_tax(incm_in, rate_level, duty_free):
    tax = 0
    if incm_in < duty_free:
        return 0
    incm = incm_in - duty_free
    for r_info in rate_level:
        if incm > r_info[0] :
            if incm >= r_info[1]:
                tax += ( r_info[1] - r_info[0] ) * r_info[2]
            else:
                tax += ( incm - r_info[0] ) * r_info[2]
        else:
            return tax
    return tax  

def get_tax_old(incm):
    return get_tax(incm, rate_level_old, duty_free_old)
 
def get_tax_new(incm):
    return get_tax(incm, rate_level_new, duty_free_new)

# 计算新旧税制下的纳税情况
# 输入参数：月收入（去除五险一金），年终奖金
# 返回值：  当前纳税额，新税制纳税额，差额
def get_tax_diff(incm, bonus=0):
    tax_old = get_tax_old(incm)
    bonus_tax = get_tax_bonus(bonus)
    tax_old = tax_old * 12 + bonus_tax
    tax_old = round(tax_old,2)
    
    monthly = incm + bonus / 12.0
    tax_new = get_tax_new(monthly) * 12
    tax_new = round(tax_new,2)
    
    diff = tax_old - tax_new    
    return (tax_old, tax_new, diff)
 

def show_tax_info(incm, bonus):
    year_incm = incm * 12 + bonus
    old, new, diff = get_tax_diff(incm,bonus)
    print("现个税：{}".format(old))
    print("新个税：{}".format(new))
    print("降税：{}".format(diff))
    print("现个税率：{}%".format(round(old/year_incm*100.0,2)))
    print("新个税率：{}%".format(round(new/year_incm*100.0,2)))


### 赶紧看看自己的税是不是降了

In [52]:
# 我是一个月薪20000，年终奖10万的码农
show_tax_info(20000, 100000)

现个税：56885.0
新个税：39080.0
降税：17805.0
现个税率：16.73%
新个税率：11.49%


In [58]:
# 老板是一个月薪8万，年终奖60万的大佬
show_tax_info(80000, 600000)

现个税：432485.0
新个税：493080.0
降税：-60595.0
现个税率：27.72%
新个税率：31.61%


### 结论很劲爆：

1. 我作为小小的码农，税果然降了不少，个税率下降了5个多百分点

2. 老板就惨了，不但没有降税，居然还要多交6万的税，税率上升了4个百分点。

**** 原来在新的税制下，并不是所有人都减税了 ****

## 第三部分：旧税制的规则及其不合理的地方

1. 年终奖累进税制，不合理

2. 可以在工资和年终奖之间调整收入结构，进行避税

下面我们用数据和图表说话


### 3.1 旧税制年终奖纳税曲线

In [48]:
bonus_arr  = list(range(0, 1000000, 500))
tax_arr    = list()
net_income = list() 
for bonus in bonus_arr:
    tax = get_tax_bonus(bonus)
    tax_arr.append(tax)
    net_income.append(bonus-tax)

from pyecharts import Line

line = Line('旧税制年终奖纳税曲线', width=800, height=600)
line.add('纳税额', bonus_arr, tax_arr, is_label_show=True)
line.add('净收入', bonus_arr, net_income, is_label_show=True)
line

### 不合理之处：在某些点，年终奖增加的时候，纳税额显著增加，导致净收入反而减少。

**** 不合理的点的位置：96万，66万，42万 ****

|年终奖|纳税额|净收入|
|-----|-----|------|
|960001|418495.45|541505.55|
|960000|330495.00|629505.00|
|660001|225495.35|434505.65|
|660000|195245.00|464755.00|


### 3.2 可以在工资和奖金之间平衡，达到最低税率

In [44]:
import numpy as np
ratio  = list(np.arange(0, 1.0, 0.01))
ratio  = [round(x, 3) for x in ratio]

def calc_tax_line(total):
    bonus  = [x * total for x in ratio]
    income = [(1-x) * total / 12.0 for x in ratio ]
    
    tax = [get_tax_old(x) for x in income]
    bonus_tax = [get_tax_bonus(x) for x in bonus]
    
    total_tax = [ round((12 * x + y)/total, 3) for (x, y) in zip(tax, bonus_tax)]
    
    return total_tax

In [47]:
from pyecharts import Line

line = Line('旧税制税率曲线（避税用）', width=800, height=600)
line.add('100万年收入', ratio, calc_tax_line(1000000), mark_point=["min"])
line.add('50万年收入', ratio, calc_tax_line(500000), mark_point=["min"])
line.add('25万年收入', ratio, calc_tax_line(250000), mark_point=["min"])
line

### 3.3 结论：

1. 对于100万年收入的人来说，最好的综合税率是0.232，基本月薪3万6左右最合适。

2. 对于50万年收入的人来说，最好的综合税率是0.19，最佳基本月薪大约是5000，其余部分发年终奖。

3. 对于25万年收入的人来说，最好的综合税率是0.128，最佳基本月薪也在5000左右，其余部分发年终奖。

## 第四部分：新税制的主要特点及税额变化情况

（一） 新税制 解决了 当前税制的上述两个主要问题

（二） 新税制 对阶梯税率进行了调整，对纳税人的纳税金额产生了影响

### 4.1  计算新老税制下的纳税情况

In [61]:
data_new = []  # 新税制税额
data_old = []  # 当前税制税额
data_diff =[]  # 税额变化量
data_pct = []  # 税额变化百分比

data_rate_new = []  # 新税制整体税率
data_rate_old = []  # 当前税制整体税率
data_rate_diff = [] # 税率变化

# 月收入区间（扣除五险一金）
incm_arr  = list(range(3500, 10000, 500)) + list(range(10000,30000,1000)) \
    + list(range(30000,50000,2000)) + list(range(50000,100000,5000))

#incm_arr = list(range(3500, 100000, 2000))    
    
# 年终奖区间
bonus_arr = list(range(0, 50000, 2000)) + list(range(50000,100000,5000)) + list(range(100000,300000,10000)) \
    + list(range(300000,500000,20000)) + list(range(500000,1000000,50000))

#bonus_arr = list(range(0, 1000000, 10000))
    
# 生成数据矩阵
for i in range(0, len(incm_arr)):
    incm = incm_arr[i]
    for j in range(0,len(bonus_arr)):
        bonus = bonus_arr[j]
        year_incm = incm * 12 + bonus
        old,new,diff = get_tax_diff( incm, bonus)
        data_diff.append([i,j,-diff])
        if(old == 0):
            data_pct.append([i,j,-100])
        else:
            data_pct.append([i,j,round(-diff/old * 100.0,2)])
        data_old.append([i,j,old])
        data_new.append([i,j,new])
        data_rate_old.append([i,j,round(old/year_incm * 100,2) ])
        data_rate_new.append([i,j,round(new/year_incm * 100,2) ])
        data_rate_diff.append([i,j,round( (new/year_incm - old/year_incm) * 100, 2) ])
    
# 获取指定的数据
# 
def get_data_arr(type_t):
    d_array = None
    if type_t == 'diff':
        d_array = data_diff     
    elif type_t == 'new':
        d_array = data_new      
    elif type_t == 'old':
        d_array = data_old       
    elif type_t == 'pct':
        d_array = data_pct
    elif type_t == 'rate_new':
        d_array = data_rate_new
    elif type_t == 'rate_old':
        d_array = data_rate_old
    elif type_t == 'rate_diff':
        d_array = data_rate_diff
    return d_array

### 4.2 当前个税税额分布热图

+ X轴：月工资收入（扣除五险一金之后）
+ Y轴：年度奖金收入

In [62]:
import random
from pyecharts import HeatMap
type_t = 'old'
d_array = get_data_arr(type_t)
    
heatmap = HeatMap()
heatmap.add("当前个税分布热图", incm_arr, bonus_arr, d_array, is_visualmap=True, 
            visual_range=[0, 500000],
            visual_orient='horizontal')
heatmap

### 4.3 新税制个税税额分布热图

In [63]:
import random
from pyecharts import HeatMap
type_t = 'new'
d_array = get_data_arr(type_t)
    
heatmap = HeatMap()
heatmap.add("新个税分布热图", incm_arr, bonus_arr, d_array, is_visualmap=True, 
            visual_range=[0, 500000],
            visual_orient='horizontal')
heatmap

### 4.4 新旧个税降幅分布热图

#### 4.4.1. 降税金额

In [64]:
import random
from pyecharts import HeatMap
type_t = 'diff'
d_array = get_data_arr(type_t)
    
heatmap = HeatMap()
heatmap.add("降税金额", incm_arr, bonus_arr, d_array, is_visualmap=True, 
            range_color = ['#313695', '#4575b4', '#74add1', '#abd9e9', '#e0f3f8', '#ffffbf',
               '#fee090', '#fdae61', '#f46d43', '#d73027', '#a50026'],
            #visual_split_number = 10,
            visual_range=[-40000, 40000],
            visual_orient='horizontal')

heatmap

### 从图中可以看出的结论：

1. 不是所有人的纳税金额都下降了，本次税改，月薪和年终奖同时都很高的人群，其实是增税的。（红色部分）

2. 月收入在2万左右，年终奖在20万左右的人群，本次减税金额较大，是很大的受益者。

3. 图中深蓝色区域的部分，减税额度最大，这类人月收入较低，但奖金极高（60万以上）。似乎是很多销售人员的收入结构。看来本次税改对销售人员最有利？


#### 4.4.2. 降税幅度

计算公式：（新税-旧税）/ 旧税

In [65]:
import random
from pyecharts import HeatMap
type_t = 'pct'
d_array = get_data_arr(type_t)

heatmap = HeatMap()
heatmap.add("降税幅度(%)", incm_arr, bonus_arr, d_array, is_visualmap=True, 
            range_color = ['#313695', '#4575b4', '#74add1', '#abd9e9', '#e0f3f8', '#ffffbf',
               '#fee090', '#fdae61', '#f46d43', '#d73027', '#a50026'],
            visual_range=[-100, 100],
            visual_orient='horizontal')

heatmap

### 结论：

1. 低收入人群降税幅度最大。

2. 高收入人群（对角线右上侧）实际上是增税的，最高增税幅度超过11%。

### 4.5 新旧税率分布热图

#### 4.5.1 当前税率分布热图

In [66]:
import random
from pyecharts import HeatMap
type_t = 'rate_old'
d_array = get_data_arr(type_t)
heatmap = HeatMap()
heatmap.add("旧税率分布图", incm_arr, bonus_arr, d_array, is_visualmap=True, 
            range_color = ['#313695', '#4575b4', '#74add1', '#abd9e9', '#e0f3f8', '#ffffbf',
               '#fee090', '#fdae61', '#f46d43', '#d73027', '#a50026'],
            visual_range=[0, 40],
            visual_orient='horizontal')
heatmap

#### 4.5.2 新税制税率分布热图

In [67]:
import random
from pyecharts import HeatMap
type_t = 'rate_new'
d_array = get_data_arr(type_t)
heatmap = HeatMap()
heatmap.add("新税率分布图", incm_arr, bonus_arr, d_array, is_visualmap=True, 
            range_color = ['#313695', '#4575b4', '#74add1', '#abd9e9', '#e0f3f8', '#ffffbf',
               '#fee090', '#fdae61', '#f46d43', '#d73027', '#a50026'],
            visual_range=[0, 40],
            visual_orient='horizontal')
heatmap


#### 4.5.3 新旧税制税率差额

In [68]:
import random
from pyecharts import HeatMap
type_t = 'rate_diff'
d_array = get_data_arr(type_t)
heatmap = HeatMap()
heatmap.add("新旧税率差额分布图", incm_arr, bonus_arr, d_array, is_visualmap=True, 
            range_color = ['#313695', '#4575b4', '#74add1', '#abd9e9', '#e0f3f8', '#ffffbf',
               '#fee090', '#fdae61', '#f46d43', '#d73027', '#a50026'],
            visual_range=[-10, 10],
            visual_orient='horizontal')
heatmap

#### 4.5.4 结论

+ 在月收入2万左右，年终奖在20万左右的人群，综合税率下降的幅度较大，达到 6-7%。（这一般是公司白领的收入区间）

+ 低工资高奖金的人群，综合税率下降幅度最大，最高可达10%。（这似乎是销售人员喜欢的方式）


# 全文结论

新税制改革是一次综合性的改革，在不考虑抵扣的情况下，具有如下特点：

## 1. 税制改进

+ 大家也许吐槽过旧税制，通过调整年终奖和月薪比例可以让你的个税税率降低。

+ 别人家的企业都通过这个来帮员工省税，但是你家公司就不帮你做这个事，于是相同的年薪情况下你一直交着比别人高的税，而新税制则彻底修复了这个问题。

+ 旧税制下税率分布不合理，例如相同月薪下，在一定范围内奖金发越多，整体税率反而会降低。而新税制下，则是严格的高收入高税率，无论怎么调整奖金和月工资都无法降低整体税率。

## 2. 为工薪阶层实打实降低了税负

+ 相对于旧税制，中低收入群体的降税还是显而易见的

+ 低收入人群的降税幅度是最大的，而中收入人群的降税金额是实打实的。

## 3. 部分高收入人群的税负增加了

+ 只有当你的年收入（月薪入加年终奖）达到80w以上才开始有增税的情况出现。


## 结尾：

+ 个税改革不是全面降税，中低收入人群少交税，高收入人群多交税，这符合税制改革的初衷。

+ 仅仅因为部分高收入人群要多交税，就说税制改革实质增税有失偏颇。

+ 个税改革是个大事情，还是要多征求人们群众的意见。

+ 下面两张图标出了增税区间，土豪们请对号入座，如果您的收入超出了这个图的范围，请理解下被贫穷限制了想象力的吃瓜群众。


In [70]:
import random
from pyecharts import HeatMap
type_t = 'rate_diff'
d_array = get_data_arr(type_t)
heatmap = HeatMap()
heatmap.add("新旧税率差额分布图", incm_arr, bonus_arr, d_array, is_visualmap=True, 
            range_color = ['#313695', '#4575b4', '#74add1', '#abd9e9', '#e0f3f8', '#ffffbf',
               '#fee090', '#fdae61', '#f46d43', '#d73027', '#a50026'],
            visual_range=[0, 10],
            visual_orient='horizontal')
heatmap